In [1]:
%jsroot on

# 将文件中的数据读入生成TGraph

In [2]:
TGraph* getdedx(string filename, int A){

    ifstream in(filename);

    auto *g = new TGraph;
    string s;
    double e, dedx;

    getline(in, s);
    int i = 0;

    while(!in.eof()){

        in >> e >> dedx;
        getline(in, s);
        if(in.eof()) break;

        g->SetPoint(i++, e*A, dedx);
    }

    in.close();
    return g;
}

# 定义获取能损的函数

In [3]:
double Z_1_8_dedx(string element, int A, double E){//定义输入量
    
    string a = "./data/";
    string b = "_si.txt";
    string c = a + element + b ; //将字符串拼接匹配文件名
    double dedx;  

    TGraph *z1 = getdedx(c, A);
    dedx = z1->Eval(E, 0, "S");
    

    
    return dedx;//返回能损值

}

# 封装计算粒子射程的函数
<font size = 4>首先对返回E-x曲线和x-E曲线的Graph进行定义，然后利用这个Graph对粒子入射的距离进行计算

In [4]:
TGraph *ex_gra(string element, int A, int choose){//设置输入量，其中choose的作用是标记返回的曲线类型

    auto *graph1 = new TGraph;
    auto *graph2 = new TGraph;
    int n = 1e8;
    double E_init = 1000., x = 0.;//设置能量初值，和位置初值

    for (int i = 0; i < n; i++){

        E_init = E_init - 100*Z_1_8_dedx(element, A, E_init);//通过迭代求出能量为0时的射程
        x = x + 0.1;

        //将数据填入Graph
        graph1->SetPoint(i, E_init, x);
        graph2->SetPoint(i, x, E_init);

        if (E_init < 0) break;
    }

    if (choose == 0) return graph1;//如果choose选择0，则返回E-x曲线
    else if (choose == 1) return graph2;//如果choose选择1，则返回x-E曲线
    else {
        return graph1;
        cout << "plz enter choose 1 or 0" << endl;
    }
}


In [5]:
double range_fun(string element, int A, double E, TGraph *g_range_fun){
    
    //if(Z > 8 || Z < 1 || Z > A) cout << "Plz enter right Z and A" << endl;

    TGraph *ele = g_range_fun;
   
    return (ele->Eval(0, 0, "S"))-(ele->Eval(E, 0, "S"));//通过E=0时对应的x值减去输入E对应的x值即为射程

}

# 封装能损计算函数
<font size = 4>由上面的函数可以得到E-x和x-E曲线，由E-x曲线可以求得x0,用x0加上探测器厚度dx可以得到x'。再用x-E曲线可以求得x'对应的E'。E-E'即为能量的损失。如果射程小于探测器厚度，那么全部能量都损失掉了。

In [6]:
double de_thick(string element, int A, double E, double thickness, TGraph *g1_de_thick, TGraph *g2_de_thick){
    
    double e_loss;

    if (range_fun( element, A, E, g1_de_thick) <= thickness ) {//如果射程小于厚度则损失所有能量

        e_loss = E;
        //cout << "Lose all energy" << endl;
    }

    else {

        TGraph *e_x_gra = g1_de_thick;//E-x曲线
        TGraph *x_e_gra = g2_de_thick;//x-E曲线

        double x0, x_prime, E_prime;

        x0 = e_x_gra->Eval(E, 0, "S");
        E_prime = x_e_gra->Eval(x0+thickness, 0, "S");//求E'

        e_loss = E - E_prime;//能量损失
    }

    return e_loss;

}

# 加入探测器分辨率
<font size = 4> 由课件内容可知，探测器分辨率与各个物理量的关系如下：$ \Delta R = 2.35 \sqrt{\frac{F\omega}{E}} $，高斯分布的$ \sigma $为 $ \sqrt{F\omega E} $，已知对于5MeV的能量分辨率为0.01，因此能量E时的高斯分布$ \sigma = \frac{0.01}{2.35} \cdot \sqrt{5E} $。其中，$ \omega $为电离能，E为能量，F是法诺因子。 
    
<font size = 4>以下函数还调整了不同分辨率进行比较，选取的分辨率为1倍硅探测器分辨，2.5倍硅探测分辨，10倍硅探测器分辨。

In [7]:
void dise_tele(){

    /* //此段程序为产生root文件所需要的程序，在notebook上运行时请注释掉，否则会严重拖慢运行速度
    double de1, de2, de3;
    double de1_blur, de2_blur, de3_blur;
    TRandom3 *ran = new TRandom3(0);
    TFile *file = new TFile("dise_tele_10.root","RECREATE");
    TTree *tree = new TTree("tree", "Ran_Events");

    tree->Branch("de1", &de1_blur, "de1/D");//对地址以及变量名进行设定
    tree->Branch("de2", &de2_blur, "de2/D");
    tree->Branch("de3", &de3_blur, "de3/D");

    for(int j = 0; j < 1000; j ++){

        int Z = ceil(ran->Uniform(0, 8));//随机产生Z值
        string res;
        stringstream ss;
        ss << Z, ss >> res;
        
        int A = 2*Z + ceil(ran->Uniform(-2, 2));随机产生A值

        auto *e_x_he = new TGraph;
        e_x_he->Clear();
        e_x_he = ex_gra(res, A, 0);
        auto *x_e_he = new TGraph;
        x_e_he->Clear();
        x_e_he = ex_gra(res, A, 1);

        for(int i =0; i < 1000; i++){
            
            double E1_he = 35*A*ran->Rndm();
            de1 = de_thick(res, A, E1_he, 1, e_x_he, x_e_he);
            de1_blur = ran->Gaus(de1, 0.01/2.35*sqrt(5*de1));//此为加入能量分辨率后的第一层能量损失
        
            double E2_he = E1_he - de1;
            de2 = de_thick(res, A, E2_he, 0.5, e_x_he, x_e_he);
            de2_blur = ran->Gaus(de2, 0.01/2.35*sqrt(5*de2));//此为加入能量分辨率后的第二层能量损失
        
            double E3_he = E2_he - de2;
            de3 = de_thick(res, A, E3_he, 1, e_x_he, x_e_he);
            de3_blur = ran->Gaus(de3, 0.01/2.35*sqrt(5*de3));//此为加入能量分辨率后的第三层能量损失

            tree->Fill();//写入成tree
    }

    }

    tree->Write();
    file->Close();
*/
    TFile *new_f = new TFile("dise_tele_1.root", "READ");//读入分辨率为硅探测器分辨率时的root文件
    TTree *new_tree = (TTree*)new_f->Get("tree");
    
    TCanvas *c1 = new TCanvas("c1", " ", 800, 600);
    c1->Divide(3,1);
    
    //绘制对比图
    c1->cd(1);
    new_tree->Draw("de1:de2>>h1(500,0,250,1000,0,500)", "de2 > 0", "colz");
    c1->cd(2);
    new_tree->Draw("de2:de3>>h2(500,0,250,500,0,250)", "de3 > 0", "colz");
    c1->cd(3);
    new_tree->Draw("de1:(de1+de2+de3)>>h3(500,0,600,500,0,500)", "de2>0&&de3>0", "colz");
    c1->Draw();
    
    TFile *new_f_2dot5 = new TFile("dise_tele_2dot5.root", "READ");//读入分辨率为2.5倍硅探测器分辨率时的root文件
    TTree *new_tree_2dot5 = (TTree*)new_f_2dot5->Get("tree");
    
    TCanvas *c2 = new TCanvas("c2", " ", 800, 600);
    c2->Divide(3,1);
    
    //绘制对比图
    c2->cd(1);
    new_tree_2dot5->Draw("de1:de2>>h1(500,0,250,1000,0,500)", "de2 > 0", "colz");
    c2->cd(2);
    new_tree_2dot5->Draw("de2:de3>>h2(500,0,250,500,0,250)", "de3 > 0", "colz");
    c2->cd(3);
    new_tree_2dot5->Draw("de1:(de1+de2+de3)>>h3(500,0,600,500,0,500)", "de2>0&&de3>0", "colz");
    c2->Draw();
    
    TFile *new_f_10 = new TFile("dise_tele_10.root", "READ");//读入分辨率为10倍硅探测器分辨率时的root文件
    TTree *new_tree_10 = (TTree*)new_f_10->Get("tree");
    
    TCanvas *c3 = new TCanvas("c3", " ", 800, 600);
    c3->Divide(3,1);
    
    //绘制对比图
    c3->cd(1);
    new_tree_10->Draw("de1:de2>>h1(500,0,250,1000,0,500)", "de2 > 0", "colz");
    c3->cd(2);
    new_tree_10->Draw("de2:de3>>h2(500,0,250,500,0,250)", "de3 > 0", "colz");
    c3->cd(3);
    new_tree_10->Draw("de1:(de1+de2+de3)>>h3(500,0,600,500,0,500)", "de2>0&&de3>0", "colz");
    c3->Draw();
    
}


In [8]:
dise_tele();

<font size = 4> 可以看到随着探测器分辨率的逐渐变差，望远镜法得到的条纹会逐渐展宽，变得越来越模糊。但是应用一倍分辨率时仍可以看到很好的分辨，这说明硅探测器的分辨率还是相当高的。这也不难理解，因为硅探测器的电离能是3.6eV，法诺因子为0.1，因此它比气体探测器的分辨率会好很多。